## Importar las librerías

In [1]:
# Importar las librerías

import numpy as np # Tratamiento numerico y matrices
import pandas as pd # Importar dataset y crear conjunto de entrenamiento y test
import torch
import torch.nn as nn # redes neuronales
import torch.nn.parallel # para crear cálculos en paralelo -> Optimización
import torch.optim as optim # Optimizador para minimizar nuestro error
import torch.utils.data
from torch.autograd import Variable

## Importar el dataset

In [2]:
# Importar el dataset

movies = pd.read_csv("ml-1m/movies.dat", sep = "::", header =None, engine = 'python', encoding = "latin-1")

In [3]:
movies.head()

0                                   1                             2
0  1                    Toy Story (1995)   Animation|Children's|Comedy
1  2                      Jumanji (1995)  Adventure|Children's|Fantasy
2  3             Grumpier Old Men (1995)                Comedy|Romance
3  4            Waiting to Exhale (1995)                  Comedy|Drama
4  5  Father of the Bride Part II (1995)                        Comedy

In [4]:
movies.shape

(3883, 3)

In [5]:
users = pd.read_csv("ml-1m/users.dat", sep = "::", header =None, engine = 'python', encoding = "latin-1")

In [6]:
users.head()

0  1   2   3      4
0  1  F   1  10  48067
1  2  M  56  16  70072
2  3  M  25  15  55117
3  4  M  45   7  02460
4  5  M  25  20  55455

In [7]:
users.shape

(6040, 5)

In [8]:
ratings = pd.read_csv("ml-1m/ratings.dat", sep = "::", header =None, engine = 'python', encoding = "latin-1")

In [9]:
ratings.head()

0     1  2          3
0  1  1193  5  978300760
1  1   661  3  978302109
2  1   914  3  978301968
3  1  3408  4  978300275
4  1  2355  5  978824291

In [10]:
ratings.shape

(1000209, 4)

## Preparar los conjuntos de entrenamiento y de testing

In [11]:
training_set = pd.read_csv( 'ml-100k/u1.base', sep ='\t', header = None)

In [12]:
training_set.shape

(80000, 4)

In [13]:
# Pytorch no acepta DataFrames sino arrays. Tenemos que reconvertirlo con numpy

training_set = np.array(training_set, dtype = "int") #no queremos que sea int64 sino int porque pytorch lo entiende mejor

In [14]:
test_set = pd.read_csv( 'ml-100k/u1.test', sep ='\t', header = None)
test_set = np.array(training_set, dtype = "int")

In [15]:
test_set.shape

(80000, 4)

## Obtener el número de usuarios y de películas

In [16]:
nb_users = int(max(max(training_set[:,0]), max(test_set[:,0])))
#Por que no sé si el usuario más alto está en el conjunto de test o de traing

In [17]:
nb_users

943

In [18]:
nb_movies = int(max(max(training_set[:,1]), max(test_set[:,1])))

In [19]:
nb_movies

1682

## Convertir los datos en un array X[u,i] con usuarios u en fila y películas

In [20]:
def convert(data):
    new_data = []
    for id_user in range(1, nb_users+1):
        id_movies = data[:,1][data[:,0]==id_user]
        id_ratings = data[:,2][data[:,0]==id_user]
        # Tb quiero un cero en las pelis que no ha clasificado -> Inicializo con 1682 ceros
        ratings = np.zeros(nb_movies)
        ratings[id_movies-1] = id_ratings
        new_data.append(list(ratings))
    return new_data
        

In [21]:
training_set = convert(training_set)

In [22]:
test_set = convert(test_set)

## Convertir los datos a tensores de Torch

Un tensor es una matriz multidimensional de un solo tipo de dato

In [23]:
training_set= torch.FloatTensor(training_set)
test_set= torch.FloatTensor(test_set)

## Parte exclusiva del AutoEncoder

## Crear la arquitectura de la Red Neuronal

In [24]:
class SAE(nn.Module): # Heredo de Module. Para acceder a funciones del "padre" usarmos "super". 
    # nn.modules es la clase base de todos los modelos de Pytorch. i no heredas de nn.Module, PyTorch no sabe que tu clase es un modelo.
    def __init__(self, ):
        super(SAE, self).__init__()#Aquí empezamos a diseñar la arquitectura de nuestra capa
        # Declaración de capas
        self.fc1 = nn.Linear(nb_movies, 20) #primera capa -(Nodos capa de entrada, Nodos Capa Oculta)- > Pasamos de 1682 nodos a 20 (fc1 -> full connection layer)
        self.fc2 = nn.Linear(20, 10)
        self.fc3 = nn.Linear(10, 20) #Primera capa de descodificación
        self.fc4 = nn.Linear(20, nb_movies) #Segunda capa de descodificación
        self.activation = nn.Sigmoid() # función que activará las neuronas
    def forward(self, x): # Propagación hacia adelante x-> Vector de datos
        x = self.activation(self.fc1(x)) # Transformo a sólo 20 caracterísitcas
        x = self.activation(self.fc2(x)) # Transformo a sólo 10 caracterísitcas
        x = self.activation(self.fc3(x)) # Decodificamos x a 20 características
        x = self.fc4(x) # Decodificamos x a su tamaño original (1682 características). En la útima capa no necesito función de activación. Porque aquí lo queremos hacer es PREDECIR
        return x
# el objeto de la clase va en minúsculas
sae = SAE()

# Criterio de optimización
criterion = nn.MSELoss()
optimizer = optim.RMSprop(sae.parameters(), lr = 0.01, weight_decay = 0.5) # lr -> Learning Rate, wight_decay -> bajada del peso original -> Como max bajar a la mitad del valor original


## Entrenar el SAE

In [ ]:
#definir el número de épocas
import math
nb_epoch = 200
for epoch in range(1 , nb_epoch +1):
    train_loss = 0 # medirá los erroes en fase de entrenamientos. La iniciamos en 0
    s= 0. # añadimos . para que sea float -> Lo usamos para calcular el RMS al final que es decimal
    for id_user in range(nb_users): # en este caso lo entrenamos de uno en uno. No por bloques
        input = Variable(training_set[id_user]).unsqueeze(0) # esto es un vector pero pytorch no acepta vectores sino arrays por bloques 
        # Para eso -> Añadimos una dimensión falsa que simule el bloque -> Variable ().unsqueeze(0) -> Para que añada la nueva dimensón en la primera posición
        target = input.clone() # clonamos el valor del vector de entrada para poder comparar el valor después de la  predicción
        # Para ahorrar memoria sólo voy  a entrenar con usuarios que valoran al menos una película
        if torch.sum(target.data > 0) > 0: # en parentesis targe.data>0 -> quito los = 0 que son los que no han valorado
            output = sae.forward(input) # Así obtenemos el pronóstico generado por el autoencoder
            target.require_grad = False # así le decimos que el target no requiere cálculos
            # voy a a seleccionar las salidas de pronósticos cuyas entradas no fueron valoradas
            output[target == 0] = 0 # Para estas salidas tampoco va a haber predicción -> Menos cálculos
            loss= criterion(output, target) # cálculo de error de pérdidas output vs target
            mean_corrector = nb_movies/float(torch.sum(target.data>0)+1e-10) #factor de corrección. Añado +1e-10 para que denominador no sea cero
            # Determina el ratio de películas que han sido valoradas
            loss.backward() # propaga el error hacia atrás
            train_loss += math.sqrt(loss.item()*mean_corrector)  # Hago la raíz por que loss.data está alm cuadrado. Esto es la suma de los errores/ Número de películas vistas
            s += 1.
            optimizer.step() #loss.backward() decida la dirección de la modificación de los pesos(aumentar o disminuir) y optimizer.step() decide la intensidad del cambio -> Por cua´nto hay que multiplicar esa dirección
        print("Epoch: " +str(epoch) + ", Loss: "+str(train_loss/s))
        
    

Epoch: 1, Loss: 3.9104346317200824
Epoch: 1, Loss: 3.9357018903009733
Epoch: 1, Loss: 3.711182778697827
Epoch: 1, Loss: 3.890880842565087
Epoch: 1, Loss: 3.763680123762234
Epoch: 1, Loss: 3.752125157464375
Epoch: 1, Loss: 3.790010534786749
Epoch: 1, Loss: 3.78436162310419
Epoch: 1, Loss: 3.8353411118284857
Epoch: 1, Loss: 3.8710614807598205
Epoch: 1, Loss: 3.8455781637379673
Epoch: 1, Loss: 3.876371699532434
Epoch: 1, Loss: 3.838633024543723
Epoch: 1, Loss: 3.8654803476216273
Epoch: 1, Loss: 3.8228505344323396
Epoch: 1, Loss: 3.8530427340320523
Epoch: 1, Loss: 3.817728860624005
Epoch: 1, Loss: 3.822466736096867
Epoch: 1, Loss: 3.8065378529008216
Epoch: 1, Loss: 3.7837367904952948
Epoch: 1, Loss: 3.74091832547867
Epoch: 1, Loss: 3.7274646727958114
Epoch: 1, Loss: 3.721381655230758
Epoch: 1, Loss: 3.7428956808734273
Epoch: 1, Loss: 3.7473566451104814
Epoch: 1, Loss: 3.715271084482357
Epoch: 1, Loss: 3.6950247051878615
Epoch: 1, Loss: 3.690648950832922
Epoch: 1, Loss: 3.694442508830551
Ep

## Testing

In [26]:
#definir el número de épocas
import math
test_loss = 0 # medirá los erroes en fase de test. La iniciamos en 0
s= 0. # añadimos . para que sea float -> Lo usamos para calcular el RMS al final que es decimal
for id_user in range(nb_users): # en este caso lo entrenamos de uno en uno. No por bloques
    input = Variable(training_set[id_user]).unsqueeze(0) # Necesitamos mantener el conj de entrenamiento. La entrada  es todo lo que el usuario ya ha visto
    
    target = Variable(test_set[id_user]).unsqueeze(0) #el objetivo ahora es predecir las puntuaciones reales en nuestro conjunto de test
    # Para ahorrar memoria sólo voy  a entrenar con usuarios que valoran al menos una película
    if torch.sum(target.data > 0) > 0: # en parentesis targe.data>0 -> quito los = 0 que son los que no han valorado
        output = sae.forward(input) # Así obtenemos el pronóstico generado por el autoencoder
        target.require_grad = False # así le decimos que el target no requiere cálculos
        # voy a a seleccionar las salidas de pronósticos cuyas entradas no fueron valoradas
        output[target == 0] = 0 # Para estas salidas tampoco va a haber predicción -> Menos cálculos
        loss= criterion(output, target) # cálculo de error de pérdidas output vs target
        mean_corrector = nb_movies/float(torch.sum(target.data>0)+1e-10) #factor de corrección. Añado +1e-10 para que denominador no sea cero
        # Determina el ratio de películas que han sido valoradas
        # Ya no pongo loss.backward() porque no estoy entrenando, no hay que propagar el error hacia atrás
        test_loss += math.sqrt(loss.item()*mean_corrector)  # Hago la raíz por que loss.data está alm cuadrado. Esto es la suma de los errores/ Número de películas vistas
        s += 1.
        # Tampoco hago optimizer.step() porque NO estoy entrenando
    print("Loss: "+str(test_loss/s))

Loss: 0.9817752300066189
Loss: 0.8882089027862459
Loss: 0.9911808559336514
Loss: 0.993896646859451
Loss: 1.0271421092579094
Loss: 1.0003371578065927
Loss: 1.009491333707421
Loss: 0.9973730324136466
Loss: 0.9929071436390914
Loss: 0.9490198664209807
Loss: 0.9420731049131951
Loss: 0.9190634471201559
Loss: 0.9406963028206116
Loss: 0.9405245683044344
Loss: 0.9541286315480831
Loss: 0.9494557077258841
Loss: 0.9474927110388471
Loss: 0.9383347770777988
Loss: 0.935174480869908
Loss: 0.9507197698315994
Loss: 0.9507005133692401
Loss: 0.9573261785886448
Loss: 0.9486384732313532
Loss: 0.9409550139854331
Loss: 0.926896455188885
Loss: 0.9165728630150363
Loss: 0.9144373762886557
Loss: 0.9120569246531716
Loss: 0.9039755071821519
Loss: 0.9043836308104342
Loss: 0.903840618623642
Loss: 0.9017826876529966
Loss: 0.890229396730335
Loss: 0.9144528401373165
Loss: 0.9123641413716929
Loss: 0.9198872684323552
Loss: 0.9180002248660801
Loss: 0.9280886446039815
Loss: 0.9338233686391205
Loss: 0.9366904406116255
Loss: 